In [1]:
# This Python 3 environment comes with many helpful analytics libraries installed
# It is defined by the kaggle/python Docker image: https://github.com/kaggle/docker-python
# For example, here's several helpful packages to load

import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)

# Input data files are available in the read-only "../input/" directory
# For example, running this (by clicking run or pressing Shift+Enter) will list all files under the input directory

import os
for dirname, _, filenames in os.walk('/kaggle/input'):
    for filename in filenames:
        print(os.path.join(dirname, filename))

# You can write up to 20GB to the current directory (/kaggle/working/) that gets preserved as output when you create a version using "Save & Run All" 
# You can also write temporary files to /kaggle/temp/, but they won't be saved outside of the current session

/kaggle/input/predict-closed-questions-on-stack-overflow/basic_benchmark.csv
/kaggle/input/predict-closed-questions-on-stack-overflow/private leaderboard raw.7z
/kaggle/input/predict-closed-questions-on-stack-overflow/train-sample_October_9_2012_v2.csv
/kaggle/input/predict-closed-questions-on-stack-overflow/public_leaderboard.zip
/kaggle/input/predict-closed-questions-on-stack-overflow/prior_benchmark.csv
/kaggle/input/predict-closed-questions-on-stack-overflow/train.zip
/kaggle/input/predict-closed-questions-on-stack-overflow/private_leaderboard.csv
/kaggle/input/predict-closed-questions-on-stack-overflow/train-sample.zip
/kaggle/input/predict-closed-questions-on-stack-overflow/train-sample.gz
/kaggle/input/predict-closed-questions-on-stack-overflow/train_October_9_2012.csv
/kaggle/input/predict-closed-questions-on-stack-overflow/private_leaderboard.7z
/kaggle/input/predict-closed-questions-on-stack-overflow/train-sample_October_9_2012_v2.7z
/kaggle/input/predict-closed-questions-on-

In [2]:
!cp /kaggle/input/predict-closed-questions-on-stack-overflow/train-sample.csv train-sample.csv

In [3]:
!ls

__notebook__.ipynb  train-sample.csv


In [4]:
import pandas as pd

data = pd.read_csv('train-sample.csv')

data.columns

Index(['PostId', 'PostCreationDate', 'OwnerUserId', 'OwnerCreationDate',
       'ReputationAtPostCreation', 'OwnerUndeletedAnswerCountAtPostTime',
       'Title', 'BodyMarkdown', 'Tag1', 'Tag2', 'Tag3', 'Tag4', 'Tag5',
       'PostClosedDate', 'OpenStatus'],
      dtype='object')

In [5]:
data.head()

PostId     PostCreationDate  OwnerUserId    OwnerCreationDate  \
0   6046168  05/18/2011 14:14:05       543315  09/17/2010 10:15:06   
1   4873911  02/02/2011 11:30:10       465076  10/03/2010 09:30:58   
2   3311559  07/22/2010 17:21:54       406143  07/22/2010 16:58:20   
3   9990413  04/03/2012 09:18:39       851755  07/19/2011 10:22:40   
4  10421966  05/02/2012 21:25:01       603588  02/04/2011 18:05:34   

   ReputationAtPostCreation  OwnerUndeletedAnswerCountAtPostTime  \
0                         1                                    2   
1                       192                                   24   
2                         1                                    0   
3                         4                                    1   
4                       334                                   14   

                                               Title  \
0  For Mongodb is it better to reference an objec...   
1  How to insert schemalocation in a xml document...   
2                            Too many lookup tables    
3                    What is this PHP code in VB.net   
4  Spring-Data mongodb querying multiple classes ...   

                                        BodyMarkdown        Tag1  \
0  I am building a corpus of indexed sentences in...     mongodb   
1  i create a xml document with JAXP and search a...         dom   
2  What are the adverse effects of having too man...  sql-server   
3  I am looking for the vb.net equivalent of this...         php   
4  With Spring-Data, you can use the @Document an...     mongodb   

              Tag2   Tag3 Tag4 Tag5       PostClosedDate     OpenStatus  
0              NaN    NaN  NaN  NaN                  NaN           open  
1              xsd   jaxp  NaN  NaN                  NaN           open  
2  database-design  enums  NaN  NaN                  NaN           open  
3           vb.net    NaN  NaN  NaN  04/15/2012 21:12:48  too localized  
4      spring-data    NaN  NaN  NaN                  NaN           open

In [6]:
data = data[['BodyMarkdown','OpenStatus']]

In [7]:
data.dropna(inplace=True)
len(data)

140272

In [8]:
!pip install transformers

In [9]:
from transformers import BertTokenizer
tokenizer = BertTokenizer.from_pretrained('bert-base-uncased', do_lower_case=True)

Downloading:   0%|          | 0.00/232k [00:00<?, ?B/s]

In [10]:
data['label']=0
data.loc[data['OpenStatus']=='open', 'label']=1
data['label'].value_counts()

0    70136
1    70136
Name: label, dtype: int64

In [11]:
import numpy as np
import tensorflow as tf

input_ids_list = []
token_type_ids = []
attention_mask_list = []
label_list = []

for bodyMarkDown,label in data[['BodyMarkdown','label']].values:
  tokenized = tokenizer.encode_plus(bodyMarkDown, add_special_tokens=True, max_length=510, pad_to_max_length=True, return_attention_mask=True)
  input_ids_list.append(tokenized['input_ids'])
  token_type_ids.append(tokenized['token_type_ids'])
  attention_mask_list.append(tokenized['attention_mask'])
  label_list.append([label])
train_ds = tf.data.Dataset.from_tensor_slices(({'input_ids':input_ids_list, 'token_type_ids':token_type_ids, 'attention_mask':attention_mask_list},label_list))

Truncation was not explicitly activated but `max_length` is provided a specific value, please use `truncation=True` to explicitly truncate examples to max length. Defaulting to 'longest_first' truncation strategy. If you encode pairs of sequences (GLUE-style) with the tokenizer you can select this strategy more precisely by providing a specific strategy to `truncation`.


/opt/conda/lib/python3.7/site-packages/transformers/tokenization_utils_base.py:2143: FutureWarning: The `pad_to_max_length` argument is deprecated and will be removed in a future version, use `padding=True` or `padding='longest'` to pad to the longest sequence in the batch, or use `padding='max_length'` to pad to a max length. In this case, you can give a specific length with `max_length` (e.g. `max_length=45`) or leave max_length to None to pad to the maximal input size of the model (e.g. 512 for Bert).
  FutureWarning,


In [12]:
from transformers import TFBertForSequenceClassification

learning_rate = 2e-05

model = TFBertForSequenceClassification.from_pretrained('bert-base-uncased')

# classifier Adam recommended
optimizer = tf.keras.optimizers.Adam(learning_rate=learning_rate, epsilon=1e-08)

# we do not have one-hot vectors, we can use sparce categorical cross entropy and accuracy
#loss = tf.keras.losses.SparseCategoricalCrossentropy(from_logits=True)
metric = tf.keras.metrics.SparseCategoricalAccuracy('accuracy')

model.compile(optimizer=optimizer, loss='binary_crossentropy', metrics=[metric])

Downloading:   0%|          | 0.00/433 [00:00<?, ?B/s]

Downloading:   0%|          | 0.00/536M [00:00<?, ?B/s]

All model checkpoint layers were used when initializing TFBertForSequenceClassification.



Some layers of TFBertForSequenceClassification were not initialized from the model checkpoint at bert-base-uncased and are newly initialized: ['classifier']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [13]:
model.summary()

Model: "tf_bert_for_sequence_classification"
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
bert (TFBertMainLayer)       multiple                  109482240 
_________________________________________________________________
dropout_37 (Dropout)         multiple                  0         
_________________________________________________________________
classifier (Dense)           multiple                  1538      
Total params: 109,483,778
Trainable params: 109,483,778
Non-trainable params: 0
_________________________________________________________________


In [14]:
history = model.fit(train_ds, epochs=1, batch_size=1)

Please report this to the TensorFlow team. When filing the bug, set the verbosity to 10 (on Linux, `export AUTOGRAPH_VERBOSITY=10`) and attach the full output.
Cause: module, class, method, function, traceback, frame, or code object was expected, got cython_function_or_method
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


The parameters `output_attentions`, `output_hidden_states` and `use_cache` cannot be updated when calling a model.They have to be set to True/False in the config object (i.e.: `config=XConfig.from_pretrained('name', output_attentions=True)`).


Cause: while/else statement not yet supported
To silence this warning, decorate the function with @tf.autograph.experimental.do_not_convert


The parameter `return_dict` cannot be set in graph mode and will always be set to `True`.


The parameters `output_attentions`, `output_hidden_states` and `use_cache` cannot be updated when calling a model.They have to be set to True/False in the config object (i.e.: `config=XConfig.from_pretrained('name', output_attentions=True)`).


...

 11611/140272 [=>............................] - ETA: 94:42:37 - loss: 0.7448 - accuracy: 0.4972

 11612/140272 [=>............................] - ETA: 94:42:33 - loss: 0.7448 - accuracy: 0.4972

 11613/140272 [=>............................] - ETA: 94:42:31 - loss: 0.7448 - accuracy: 0.4972

 11614/140272 [=>............................] - ETA: 94:42:27 - loss: 0.7448 - accuracy: 0.4972

 11615/140272 [=>............................] - ETA: 94:42:24 - loss: 0.7448 - accuracy: 0.4972